In [3]:
import numpy as np
import json
import pandas as pd
import cv2
import os
import shutil
import matplotlib.pyplot as plt
from PIL import Image

from keras.layers import Input,Conv2D,MaxPool2D,Dense,Flatten,BatchNormalization,Normalization
from keras.preprocessing.image import ImageDataGenerator
from keras.models import Model
from keras.callbacks import EarlyStopping

import tensorflow as tf


Loading data

In [4]:
with open(r"D:\Datasets\facial_landmark_dataset\all_data.json",'r') as file:
    data = json.load(file)
file.close()

In [5]:
columns = ['0_x', '0_y', '1_x', '1_y', '2_x', '2_y', '3_x', '3_y', '4_x', '4_y', '5_x', '5_y', '6_x', '6_y', '7_x', '7_y', '8_x', '8_y', '9_x', '9_y', '10_x', '10_y',
           '11_x', '11_y', '12_x', '12_y', '13_x', '13_y', '14_x', '14_y', '15_x', '15_y', '16_x', '16_y', '17_x', '17_y', '18_x', '18_y', '19_x', '19_y', '20_x', '20_y', 
           '21_x', '21_y', '22_x', '22_y', '23_x', '23_y', '24_x', '24_y', '25_x', '25_y', '26_x', '26_y', '27_x', '27_y', '28_x', '28_y', '29_x', '29_y', '30_x', '30_y', 
           '31_x', '31_y', '32_x', '32_y', '33_x', '33_y', '34_x', '34_y', '35_x', '35_y', '36_x', '36_y', '37_x', '37_y', '38_x', '38_y', '39_x', '39_y', '40_x', '40_y', 
           '41_x', '41_y', '42_x', '42_y', '43_x', '43_y', '44_x', '44_y', '45_x', '45_y', '46_x', '46_y', '47_x', '47_y', '48_x', '48_y', '49_x', '49_y', '50_x', '50_y', 
           '51_x', '51_y', '52_x', '52_y', '53_x', '53_y', '54_x', '54_y', '55_x', '55_y', '56_x', '56_y', '57_x', '57_y', '58_x', '58_y', '59_x', '59_y', '60_x', '60_y', 
           '61_x', '61_y', '62_x', '62_y', '63_x', '63_y', '64_x', '64_y', '65_x', '65_y', '66_x', '66_y', '67_x', '67_y','image_name']

In [6]:
def extract_landmark_data(data):
    extracted_data = []
    for face_data in data.values():
        landmark_data = []
        for index,landmarks in enumerate(face_data['face_landmarks']):
            landmark_dict = {f'{index}_x' : landmarks[0], f'{index}_y' : landmarks[1]}
            landmark_data.append(landmark_dict)
        extracted_data.append({
            'face_landmark' : landmark_data,
            'file_name' : face_data['file_name']
        })
    return extracted_data

In [7]:
dataset = []

for face_data in data.values():
    temp = []
    for index,landmarks in enumerate(face_data['face_landmarks']):
        for i in landmarks:
            temp.append(i)
    temp.append(face_data['file_name'])
    dataset.append(temp)

In [8]:
dataset

[[73.7203007518797,
  237.71428571428572,
  81.03458646616541,
  276.2105263157895,
  88.34887218045112,
  312.78195488721803,
  102.20751879699247,
  347.81353383458645,
  128.0,
  375.1458646616541,
  161.10676691729324,
  393.2390977443609,
  198.44812030075187,
  405.17293233082705,
  229.63007518796994,
  418.26165413533835,
  259.27218045112784,
  420.57142857142856,
  284.29473684210524,
  412.8721804511278,
  305.46766917293235,
  396.70375939849623,
  329.7203007518797,
  381.30526315789473,
  349.73834586466165,
  357.82255639097747,
  362.0571428571429,
  329.33533834586467,
  366.6766917293233,
  298.53834586466166,
  367.44661654135336,
  267.74135338345866,
  367.8315789473684,
  237.3293233082707,
  134.1593984962406,
  211.9218045112782,
  158.02706766917294,
  196.13834586466166,
  188.05413533834587,
  188.05413533834587,
  221.1609022556391,
  188.82406015037594,
  250.03308270676692,
  197.29323308270676,
  284.6796992481203,
  198.44812030075187,
  306.237593984962

In [9]:
df = pd.DataFrame(data=dataset,columns=columns)

In [10]:
df.shape

(5000, 137)

In [11]:
df.head()

0_x         0_y         1_x         1_y         2_x         2_y  \
0   73.720301  237.714286   81.034586  276.210526   88.348872  312.781955   
1  127.065693  233.265207  125.819951  270.014599  125.819951  306.141119   
2  104.102613  213.069834  104.102613  251.986698  107.021378  291.876485   
3  131.883228  219.805381  128.366342  253.801946  128.952490  287.798512   
4  137.156540  233.089494  135.930560  268.642921  138.382520  304.196348   

          3_x         3_y         4_x         4_y  ...        63_y  \
0  102.207519  347.813534  128.000000  375.145865  ...  343.963910   
1  127.688564  342.267640  136.408759  377.148418  ...  368.428224   
2  114.804751  327.874584  131.344418  359.008076  ...  359.980998   
3  131.883228  320.622782  143.606182  350.516314  ...  363.411563   
4  143.286441  339.136785  156.159234  371.012272  ...  385.111045   

         64_x        64_y        65_x        65_y        66_x        66_y  \
0  297.383459  349.738346  283.524812  351.278195  275.055639  352.818045   
1  308.321168  369.673966  260.360097  402.063260  239.182482  403.309002   
2  297.714014  358.035154  267.553444  360.953919  255.878385  361.926841   
3  274.317115  366.928449  250.285060  368.686892  240.906697  369.273039   
4  289.178090  382.659084  262.819515  389.401975  248.720742  391.853936   

         67_x        67_y  image_name  
0  265.431579  352.818045   00000.png  
1  218.627737  397.080292   00001.png  
2  243.230404  360.953919   00002.png  
3  233.286777  366.342301   00003.png  
4  234.008979  388.788985   00004.png  

[5 rows x 137 columns]

In [12]:
df.to_csv("facial_landmarks.csv",index=False)

In [13]:
# plotting coordinates on the image

# image_path = r"D:\Datasets\facial_landmark_dataset\images\00000.png"

# # Read the image using cv2.imread()
# image = cv2.imread(image_path)

# # Check if image reading was successful
# if image is None:
#   print("Error: Could not read image from", image_path)
#   exit()

In [14]:
coordinates = df.iloc[0,:-1].values

In [15]:
coord = []

for i in range(0,len(coordinates),2):
        coord.append((coordinates[i], coordinates[i + 1]))

Testing Coordinates

In [16]:
# point_color = (255, 0, 0)
# coordinate = (50, 50)  # Example coordinate (x, y)
# font = cv2.FONT_HERSHEY_SIMPLEX
# font_scale = 10
# color = (255, 255, 255)  # White color in BGR format
# thickness = 1

# for i,(x, y) in enumerate(coord):
#   # Draw a circle with radius 5 and -1 thickness for filled circle
#   image = cv2.circle(image, (int(x), int(y)), 2, point_color, -1)
#   # cv2.putText(image, f"{i}", (int(x)+1, int(y)+1), font, 0, color, thickness)
# cv2.imshow("sample",image)
# cv2.waitKey(0)
# cv2.destroyAllWindows()

Loading Dataset

In [17]:
landmark_dataset = pd.read_csv(r"D:\vs code\python\DeepLearning\Projects\Facial_landmark_detection\facial_landmarks.csv")

In [18]:
landmark_dataset.head()

0_x         0_y         1_x         1_y         2_x         2_y  \
0   73.720301  237.714286   81.034586  276.210526   88.348872  312.781955   
1  127.065693  233.265207  125.819951  270.014599  125.819951  306.141119   
2  104.102613  213.069834  104.102613  251.986698  107.021378  291.876485   
3  131.883228  219.805381  128.366342  253.801946  128.952490  287.798512   
4  137.156540  233.089494  135.930560  268.642921  138.382520  304.196348   

          3_x         3_y         4_x         4_y  ...        63_y  \
0  102.207519  347.813534  128.000000  375.145865  ...  343.963910   
1  127.688564  342.267640  136.408759  377.148418  ...  368.428224   
2  114.804751  327.874584  131.344418  359.008076  ...  359.980998   
3  131.883228  320.622782  143.606182  350.516314  ...  363.411563   
4  143.286441  339.136785  156.159234  371.012272  ...  385.111045   

         64_x        64_y        65_x        65_y        66_x        66_y  \
0  297.383459  349.738346  283.524812  351.278195  275.055639  352.818045   
1  308.321168  369.673966  260.360097  402.063260  239.182482  403.309002   
2  297.714014  358.035154  267.553444  360.953919  255.878385  361.926841   
3  274.317115  366.928449  250.285060  368.686892  240.906697  369.273039   
4  289.178090  382.659084  262.819515  389.401975  248.720742  391.853936   

         67_x        67_y  image_name  
0  265.431579  352.818045   00000.png  
1  218.627737  397.080292   00001.png  
2  243.230404  360.953919   00002.png  
3  233.286777  366.342301   00003.png  
4  234.008979  388.788985   00004.png  

[5 rows x 137 columns]

In [19]:
# folder_path = r"D:\Datasets\facial_landmark_dataset\images"

# all_images = os.listdir(folder_path)

In [20]:
# let the image split ratio be 70/15/15

train_folder = r"D:\Datasets\facial_landmark_dataset\train"
test_folder =  r"D:\Datasets\facial_landmark_dataset\test"
val_folder = r"D:\Datasets\facial_landmark_dataset\validation"

os.makedirs(train_folder,exist_ok=True)
os.makedirs(test_folder,exist_ok=True)
os.makedirs(val_folder,exist_ok=True)


In [21]:
# for image in range(3500):
#     source_path = os.path.join(folder_path,all_images[image])
#     destination_path = os.path.join(train_folder,all_images[image])
#     shutil.move(source_path,destination_path)
    
# all_images = os.listdir(folder_path)

# for image in range(750):
#     source_path = os.path.join(folder_path,all_images[image])
#     destination_path = os.path.join(test_folder,all_images[image])
#     shutil.move(source_path,destination_path)

# all_images = os.listdir(folder_path)

# for image in all_images:
#     source_path = os.path.join(folder_path,image)
#     destination_path = os.path.join(val_folder,image)
#     shutil.move(source_path,destination_path)   


In [22]:
train_images = os.listdir(train_folder)
test_images = os.listdir(test_folder)
val_images = os.listdir(val_folder)

In [23]:
train_landmark_coordinates = landmark_dataset.iloc[:4500,:]
val_landmark_coordinates = landmark_dataset.iloc[4500:5000,:]

In [24]:
train_landmark_coordinates.to_csv("training_data_coordinates.csv")
val_landmark_coordinates.to_csv("validation_data_coordinates.csv")


Viewing Images

In [25]:
# test_images = os.listdir(val_folder)

# for index,image in enumerate(val_images):
#     path = os.path.join(val_folder,image)
#     coordinates = val_landmark_coordinates.iloc[index,:-1].values
#     image = Image.open(path)
#     image = np.array(image)
#     plt.imshow(image)
#     coord = []
#     for i in range(0,len(coordinates),2):
#         coord.append((coordinates[i], coordinates[i + 1]))
#         x_coords, y_coords = zip(*coord)
#     plt.scatter(x_coords, y_coords,s=1,color='darkblue')
#     plt.show()



# all the images are perfectly fine

In [26]:
train_landmark_coordinates.shape

(4500, 137)

In [27]:
val_landmark_coordinates.shape

(500, 137)

In [28]:
# getting to know to dimensions of the dataset images

# image = cv2.imread(os.path.join(train_folder,"00000.png"),0)

# cv2.imshow("image",image)
# cv2.waitKey(0)
# cv2.destroyAllWindows()

In [29]:
training_path  = "D://Datasets//facial_landmark_dataset//train"

In [30]:
train_data = []

for image_name in train_images:
    image_path = os.path.join(train_folder, image_name)
    img = Image.open(image_path)
    img_gray = img.convert('L')
    img = img_gray.resize((224,224))
    train_data.append(img)

validation_data = []

for image_name in val_images:
    image_path = os.path.join(val_folder, image_name)
    img = Image.open(image_path)
    img_gray = img.convert('L')
    img = img_gray.resize((224,224))
    validation_data.append(img)

In [31]:
train_data = np.array(train_data)
validation_data = np.array(validation_data)

In [32]:

train_data = train_data.astype(np.float32) / 255.0
validation_data = validation_data.astype(np.float32) / 255.0

In [33]:
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

Num GPUs Available:  0


Creating Neural Network

In [34]:
# input_layer = Input(shape=(224,224,1),name="input_layer")

# conv_1 = Conv2D(32,kernel_size=(3,3),activation='relu',padding="same",name="conv_1")(input_layer)
# conv_2 = Conv2D(32,kernel_size=(3,3),activation='relu',padding="same",name="conv_2")(conv_1)
# pool_1 = MaxPool2D(pool_size=(2,2),strides=(2,2),name="pool_1")(conv_2)

# conv_3 = Conv2D(64,kernel_size=(3,3),activation='relu',padding="same",name="conv_3")(pool_1)
# conv_4 = Conv2D(64,kernel_size=(3,3),activation='relu',padding="same",name="conv_4")(conv_3)
# conv_5 = Conv2D(64,kernel_size=(3,3),activation='relu',padding="same",name = "conv_5")(conv_4)
# pool_2 = MaxPool2D(pool_size=(2,2),strides=(2,2),name="pool_2")(conv_5)
# dropout_1 = Dropout(0.1)(pool_2)

# conv_6 = Conv2D(128,kernel_size=(3,3),activation='relu',padding="same",name="conv_6")(dropout_1)
# conv_7 = Conv2D(128,kernel_size=(3,3),activation='relu',padding="same",name="conv_7")(conv_6)
# conv_8 = Conv2D(128,kernel_size=(3,3),activation='relu',padding="same",name="conv_8")(conv_7)
# pool_3 = MaxPool2D(pool_size=(2,2),strides=(2,2),name="pool_3")(conv_8)
# dropout_2 = Dropout(0.1)(pool_3)

# conv_9 = Conv2D(256,kernel_size=(3,3),activation='relu',padding="same",name="conv_9")(dropout_2)
# conv_10 = Conv2D(256,kernel_size=(3,3),activation='relu',padding="same",name="conv_10")(conv_9)
# conv_11 = Conv2D(256,kernel_size=(3,3),activation='relu',padding="same",name="conv_11")(conv_10)
# pool_4 = MaxPool2D(pool_size=(2,2),strides=(2,2),name="pool_4")(conv_11)
# dropout_3 = Dropout(0.1)(pool_4)

# conv_12 = Conv2D(512,kernel_size=(3,3),activation='relu',padding="same",name="conv_12")(dropout_3)
# conv_13 = Conv2D(512,kernel_size=(3,3),activation='relu',padding="same",name="conv_13")(conv_12)
# conv_14 = Conv2D(512,kernel_size=(3,3),activation='relu',padding="same",name="conv_14")(conv_13)
# pool_5 = MaxPool2D(pool_size=(2,2),strides=(2,2),name="pool_5")(conv_14)
# dropout_4 = Dropout(0.1)(pool_5)

# flatten = Flatten()(dropout_4)

# dense_1 = Dense(1024,activation="relu", name="dense_1")(flatten)
# dense_2 = Dense(1024,activation='relu', name="dense_2")(dense_1)
# dense_3 = Dense(512,activation='relu', name="dense_3")(dense_2)

# dense_output = Dense(136, name="output_layer")(dense_3)


# model = Model(input_layer,dense_output)

In [35]:
input_shape = shape=(224,224,1)
output_size = 136

preprocess = Normalization()

# Convolutional layers.
conv_1 = Conv2D(filters=32,
                                kernel_size=(3, 3),
                                activation='relu')
conv_2 = Conv2D(filters=64,
                                kernel_size=(3, 3),
                                strides=(1, 1),
                                padding='valid',
                                activation='relu')
conv_3 = Conv2D(filters=64,
                                kernel_size=(3, 3),
                                strides=(1, 1),
                                padding='valid',
                                activation='relu')
conv_4 = Conv2D(filters=64,
                                kernel_size=(3, 3),
                                strides=(1, 1),
                                padding='valid',
                                activation='relu')
conv_5 = Conv2D(filters=64,
                                kernel_size=[3, 3],
                                strides=(1, 1),
                                padding='valid',
                                activation='relu')
conv_6 = Conv2D(filters=128,
                                kernel_size=(3, 3),
                                strides=(1, 1),
                                padding='valid',
                                activation='relu')
conv_7 = Conv2D(filters=128,
                                kernel_size=[3, 3],
                                strides=(1, 1),
                                padding='valid',
                                activation='relu')
conv_8 = Conv2D(filters=256,
                                kernel_size=[3, 3],
                                strides=(1, 1),
                                padding='valid',
                                activation='relu')

# Pooling layers.
pool_1 = MaxPool2D(pool_size=(2, 2),
                                strides=(2, 2),
                                padding='valid')
pool_2 = MaxPool2D(pool_size=(2, 2),
                                strides=(2, 2),
                                padding='valid')
pool_3 = MaxPool2D(pool_size=(2, 2),
                                strides=(2, 2),
                                padding='valid')
pool_4 = MaxPool2D(pool_size=[2, 2],
                                strides=(1, 1),
                                padding='valid')

# Dense layers.
dense_1 = Dense(units=1024,
                                activation='relu',
                                use_bias=True)
dense_2 = Dense(units=output_size,
                                activation=None,
                                use_bias=True)

# Batch norm layers
bn_1 = BatchNormalization()
bn_2 = BatchNormalization()
bn_3 = BatchNormalization()
bn_4 = BatchNormalization()
bn_5 = BatchNormalization()
bn_6 = BatchNormalization()
bn_7 = BatchNormalization()
bn_8 = BatchNormalization()
bn_9 = BatchNormalization()


# Flatten layers.
flatten_1 = Flatten()

# All layers got. Define the forward propgation.
inputs = Input(shape=input_shape, name="image_input")

# Preprocess the inputs.
x = preprocess(inputs)

# |== Layer 1 ==|
x = conv_1(x)
x = bn_1(x)
x = pool_1(x)

# |== Layer 2 ==|
x = conv_2(x)
x = bn_2(x)
x = conv_3(x)
x = bn_3(x)
x = pool_2(x)

# |== Layer 3 ==|
x = conv_4(x)
x = bn_4(x)
x = conv_5(x)
x = bn_5(x)
x = pool_3(x)

# |== Layer 4 ==|
x = conv_6(x)
x = bn_6(x)
x = conv_7(x)
x = bn_7(x)
x = pool_4(x)

# |== Layer 5 ==|
x = conv_8(x)
x = bn_8(x)

# |== Layer 6 ==|
x = flatten_1(x)
x = dense_1(x)
x = bn_9(x)
outputs = dense_2(x)

# Return the model
model = Model(inputs=inputs, outputs=outputs, name="landmark")

In [36]:
model.compile(optimizer="adam",loss='mean_squared_error',metrics=['accuracy'])

In [37]:
model.summary()

Model: "landmark"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 image_input (InputLayer)    [(None, 224, 224, 1)]     0         
                                                                 
 normalization (Normalizati  (None, 224, 224, 1)       3         
 on)                                                             
                                                                 
 conv2d (Conv2D)             (None, 222, 222, 32)      320       
                                                                 
 batch_normalization (Batch  (None, 222, 222, 32)      128       
 Normalization)                                                  
                                                                 
 max_pooling2d (MaxPooling2  (None, 111, 111, 32)      0         
 D)                                                              
                                                          

In [38]:
early_stopping_callback = EarlyStopping(monitor='val_loss', patience=3)

In [40]:
model.fit(train_data,train_landmark_coordinates.iloc[:,:-1].values.astype(np.float32),validation_data=(validation_data,val_landmark_coordinates.iloc[:,:-1].values.astype(np.float32)),batch_size=64,verbose=1,epochs=100, callbacks=early_stopping_callback)

Epoch 1/100
48/71 [===================>..........] - ETA: 27s - loss: 50741.6836 - accuracy: 0.0583

KeyboardInterrupt: 

In [ ]:
model.save("facial_detection_model_3.h5")

c:\Users\Omen\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\engine\training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(
